##setup

In [ ]:
%%capture
!pip install transformers
!pip install shap

In [ ]:
from transformers import BertForSequenceClassification, BertTokenizer
from transformers import AutoModelForSequenceClassification, AutoTokenizer
import shap

In [ ]:

import torch
import pickle
import pandas as pd
import numpy as np

import scipy as sp
import os
import random

In [ ]:
path='/content/drive/MyDrive/fake-news-adversarial-benchmark/'
# Define paths liar
"""
dataset='LIAR'
model_path = path+'Model/liar_model2'
path_data_created='/content/drive/MyDrive/fake-news-adversarial-benchmark/data_created/liar/'
path_csv= path_data_created+'liar_1000.csv'
shap_path=path_data_created+'shapvalues_1000_liar.sav'
path_labels=path_data_created+'labels_liar.npy'
outputs_path=path_data_created+'original_probs_liar_1000.pt'
"""
# Define paths Fake News

dataset='Fake News'
model_path = path+'Model/fn_model'
path_data_created='/content/drive/MyDrive/fake-news-adversarial-benchmark/data_created/fake_news/'
path_csv= path_data_created+'fake_news_1000.csv'
path_labels=path_data_created+'labels_fake_news.npy'
shap_path=path_data_created+'shapvalues_1000_fake_news.sav'
outputs_path=path_data_created+'original_outputs_fake_news_1000.pt'
"""
# Define paths imdb

dataset='IMDB'
path_data_created='/content/drive/MyDrive/fake-news-adversarial-benchmark/data_created/imdb/'
path_csv= path_data_created+'imdb_1000.csv'
path_labels=path_data_created+'labels_imdb.npy'
shap_path=path_data_created+'shapvalues_1000_imdb.sav'
outputs_path=path_data_created+'original_probs_imdb_1000.pt'
"""

"\n# Define paths imdb\n\ndataset='IMDB'\npath_data_created='/content/drive/MyDrive/fake-news-adversarial-benchmark/data_created/imdb/'\npath_csv= path_data_created+'imdb_1000.csv'\npath_labels=path_data_created+'labels_imdb.npy'\nshap_path=path_data_created+'shapvalues_1000_imdb.sav' \noutputs_path=path_data_created+'original_probs_imdb_1000.pt'\n"

In [ ]:
# Load the tokenizer and model
if dataset == 'IMDB':
  print('Using IMDB trained model and Tokenizer')
  !pip install textattack
  tokenizer = AutoTokenizer.from_pretrained("textattack/bert-base-uncased-imdb")
  model = AutoModelForSequenceClassification.from_pretrained("textattack/bert-base-uncased-imdb")
else:
  print('Using '+str(model_path)+' model')
  tokenizer = BertTokenizer.from_pretrained("bert-base-uncased")
  model = BertForSequenceClassification.from_pretrained(model_path,  num_labels = 2)

Using /content/drive/MyDrive/fake-news-adversarial-benchmark/Model/fn_model model


In [ ]:
device = torch.device(str("cuda:0") if torch.cuda.is_available() else "cpu")
model = model.to(device)

In [ ]:
path_final=path+'final_files/'+dataset+'/'
path_perturbed=path_data_created+'perturbed/'

df = pd.read_csv(path_csv)
labels = np.load(path_labels)
shap_values = pickle.load(open(shap_path, 'rb'))
original_probs= torch.load(outputs_path, map_location=torch.device('cpu'))
labels=torch.LongTensor(labels)

###prepare/load data

In [ ]:
np.random.seed(42)
rand_index= np.random.randint(0, high=1000, size=350)
rand_index

array([102, 435, 860, 270, 106,  71, 700,  20, 614, 121, 466, 214, 330,
       458,  87, 372,  99, 871, 663, 130, 661, 308, 769, 343, 491, 413,
       805, 385, 191, 955, 276, 160, 459, 313,  21, 252, 747, 856, 560,
       474,  58, 510, 681, 475, 699, 975, 782, 189, 957, 686, 957, 562,
       875, 566, 243, 831, 504, 130, 484, 818, 646,  20, 840, 166, 273,
       387, 600, 315,  13, 241, 776, 345, 564, 897, 339,  91, 366, 955,
       454, 427, 508, 775, 942,  34, 205,  80, 931, 561, 871, 387,   1,
       389, 565, 105, 771, 821, 476, 702, 401, 729, 555, 161, 201, 957,
       995, 269, 862, 815, 270, 455, 461, 726, 251, 701, 295, 724, 719,
       748, 337, 878,  52, 791, 921, 216, 763, 187, 379, 492,  40, 156,
        14, 812,  64, 856, 838, 520, 343, 128, 647, 471,  62, 138, 498,
       592, 391, 674, 418, 288, 378, 772, 489, 230,  40,  27, 134, 200,
       839, 779, 929,  32,  47, 502, 406, 573, 727, 804,  98, 683, 871,
       725, 986, 546, 960, 738, 612, 942, 461, 642, 768,   4, 21

In [ ]:
"""
perturbed_texts = []
original_shaps = []
ind=[]
#path_data='/content/drive/MyDrive/fake-news-adversarial-benchmark/data_created/liar/LIAR'
for i in rand_index:
  file_path = path_perturbed + dataset+ '_' + str(i) + '_augmented.npy'
  if os.path.exists(file_path):
    perturbed_texts.append(np.load(file_path))
    original_shaps.append(shap_values[i])
    ind.append(i)
  else:
    continue

np.save(path_perturbed+dataset+'_all_perturbed.npy', perturbed_texts)
pickle.dump(original_shaps, open(path_perturbed+dataset+'_all_perturbed_original_shap.sav', 'wb'))
np.save(path_perturbed+dataset+'_all_perturbed_ind.npy', ind)

"""

"\nperturbed_texts = []\noriginal_shaps = []\nind=[]\n#path_data='/content/drive/MyDrive/fake-news-adversarial-benchmark/data_created/liar/LIAR'\nfor i in rand_index:\n  file_path = path_perturbed + dataset+ '_' + str(i) + '_augmented.npy'\n  if os.path.exists(file_path):\n    perturbed_texts.append(np.load(file_path))\n    original_shaps.append(shap_values[i])\n    ind.append(i)\n  else:\n    continue\n\nnp.save(path_perturbed+dataset+'_all_perturbed.npy', perturbed_texts)\npickle.dump(original_shaps, open(path_perturbed+dataset+'_all_perturbed_original_shap.sav', 'wb'))\nnp.save(path_perturbed+dataset+'_all_perturbed_ind.npy', ind)\n\n"

In [ ]:
perturbed_texts= np.load(path_perturbed+dataset+'_all_perturbed.npy', allow_pickle=True)
original_shaps= pickle.load(open(path_perturbed+dataset+'_all_perturbed_original_shap.sav', 'rb'))
ind= np.load(path_perturbed+dataset+'_all_perturbed_ind.npy', allow_pickle=True)

"""
original_shaps = []
for i in ind:
  original_shaps.append(shap_values[i])
  """

'\noriginal_shaps = []\nfor i in ind:\n  original_shaps.append(shap_values[i])\n  '

In [ ]:
lipschitz_sample = df.iloc[ind]['statement'].copy().tolist()
lipschitz_sample[:10]

['20 wines for under $20: the fall edition - the new york times',
 'have the dallas police improved? depends on whom you ask - the new york times',
 'how we can win the propaganda war',
 'russian grannies make deal with lipton',
 'counter terror police arrest man carrying axe, knives near uk army base',
 "swedish pensioner prosecuted for 'hate' for accusing migrants of arson",
 'broad challenge to trump order may center on cleveland doctor - the new york times',
 'marks and spencer to turn high street stores into bingo halls',
 'texas elector expects massive corruption related to the electoral college vote',
 'hundreds of pounds lighter, and now shedding another burden of the past - the new york times']

In [ ]:
print(perturbed_texts[0][:10])
print(lipschitz_sample[0])
print(original_shaps[0])

['000 wines for under $20: the fall edition - the new york times'
 '1 wines for under $20: the fall edition - the new york times'
 '10 wines for under $20: the fall edition - the new york times'
 '100 wines for under $20: the fall edition - the new york times'
 '15 wines for under $20: the fall edition - the new york times'
 '1920 wines for under $20: the fall edition - the new york times'
 '2 wines for under $20: the fall edition - the new york times'
 '20 and for under $20: the fall edition - the new york times'
 '20 bordeaux for under $20: the fall edition - the new york times'
 '20 bottles for under $20: the fall edition - the new york times']
20 wines for under $20: the fall edition - the new york times
.values =
array([ 0.        ,  0.00490105,  0.00268453,  0.00688738,  0.00365818,
        0.00770843,  0.0048399 ,  0.00829434,  0.0130564 ,  0.00249624,
        0.00745153,  0.0097388 ,  0.00669724, -0.00151104, -0.00126433,
       -0.00331485,  0.        ])

.base_values =
10.309

In [ ]:
random.seed(42)
for sublist in perturbed_texts:
    random.shuffle(sublist)
perturbed_texts[0][:10]

array(['20 wines for under $20: the fall edition - the financial york times',
       '20 wines for under $20: the fall edition - the new baltimore times',
       '20 wines for under $r: the fall edition - the new york times',
       '20 wines for under $20: the fall edition - top new york times',
       '20 and for under $20: the fall edition - the new york times',
       '20 wines found under $20: the fall edition - the new york times',
       '20 wines worth under $20: the fall edition - the new york times',
       '20 wines only under $20: the fall edition - the new york times',
       '20 wines for under $20: the next edition - the new york times',
       '20 wines for under $20: the fall edition - the new herald times'],
      dtype='<U70')

##SHAP

In [ ]:
# define a prediction function https://shap.readthedocs.io/en/latest/example_notebooks/overviews/An%20introduction%20to%20explainable%20AI%20with%20Shapley%20values.html#nlp_model
def f(x):
    tv = torch.tensor([tokenizer.encode(v, padding='max_length', max_length=512, add_special_tokens=False ) for v in x]).to(device)
    outputs = model(tv)[0].detach().cpu().numpy()
    scores = (np.exp(outputs).T / np.exp(outputs).sum(-1)).T
    val = sp.special.logit(scores[:,1]) # use one vs rest logit units
    return val

explainer = shap.Explainer(f, tokenizer)

##from saved TextAttack
based on Naylor et al. https://github.com/mnaylor5/quantifying-explainability

###definitions

In [ ]:
def filter_token(tokens):
  mask = np.logical_and(tokens != 101, tokens != 102)
  mask = np.logical_and(mask, tokens != 0)
  return tokens[mask]

def decode_tokens(tokens):
  string = tokenizer.decode(tokens)
  return string

def filter_decode_tokens(tokens):
  mask = np.logical_and(tokens != 101, tokens != 102)
  mask = np.logical_and(mask, tokens != 0)
  string = tokenizer.decode(tokens[mask])
  return string

In [ ]:
def local_lipschitz_torch(original_exp, perturbed_exp, distance):
    # this function is set up to do individual (non-batched) calculations for pytorch tensors
    return torch.norm(original_exp - perturbed_exp).item() / distance

def local_lipschitz(original_exp, perturbed_exp, distance):
    # original_exp (# features) - perturbed_exps (# neighbors, # features) will broadcast across neighbors
    # --- note: this assumes that the perturbed_exp array represents as many documents as input_distances (for the division by distance)
    # taking L2 norm over axis=-1 will return the L2 norm for each perturbed neighbor
    # divide by euclidean distances for each neighbor to get a vector of (# neighbors)
    return np.linalg.norm(original_exp - perturbed_exp, axis=-1) / np.array(distance)

###check distance to determine EPSILON

In [ ]:
"""
d=[]
metrics = []
for i in range(len(lipschitz_sample)):
  print(i)
  d_i=[]
  original_tokens=tokenizer(lipschitz_sample[i], return_tensors='pt')['input_ids']
  original_text=filter_decode_tokens(original_tokens)
  original_embeds = model.bert.embeddings(original_tokens.to(device))
  j=0
  while j < (len(perturbed_texts[i])-1):  #(len(perturbed_texts[i]))
    perturbed_text=perturbed_texts[i][j]
    perturbed_tokens = tokenizer(perturbed_text, return_tensors='pt')['input_ids']
    while len(perturbed_tokens[0]) != len(original_tokens[0]):
      perturbed_tokens =  tokenizer(perturbed_texts[i][j], return_tensors='pt')['input_ids']
      j+=1
    perturbed_embeds = model.bert.embeddings(perturbed_tokens.to(device))
    d_ij = torch.norm(original_embeds - perturbed_embeds).item() / original_embeds.squeeze().size(0)
    j+=1
    d_i.append(d_ij)
  d.append(d_i)

np.save(path_perturbed+dataset+'_distances.npy', d)
"""

"\nd=[]\nmetrics = []\nfor i in range(len(lipschitz_sample)): \n  print(i)\n  d_i=[]\n  original_tokens=tokenizer(lipschitz_sample[i], return_tensors='pt')['input_ids']\n  original_text=filter_decode_tokens(original_tokens)\n  original_embeds = model.bert.embeddings(original_tokens.to(device))\n  j=0\n  while j < (len(perturbed_texts[i])-1):      \n    perturbed_text=perturbed_texts[i][j] \n    perturbed_tokens = tokenizer(perturbed_text, return_tensors='pt')['input_ids']\n    while len(perturbed_tokens[0]) != len(original_tokens[0]):\n      perturbed_tokens =  tokenizer(perturbed_texts[i][j], return_tensors='pt')['input_ids']\n      j+=1\n    perturbed_embeds = model.bert.embeddings(perturbed_tokens.to(device))\n    d_ij = torch.norm(original_embeds - perturbed_embeds).item() / original_embeds.squeeze().size(0)\n    j+=1\n    d_i.append(d_ij)\n  d.append(d_i) \n\nnp.save(path_perturbed+dataset+'_distances.npy', d)\n"

In [ ]:
d = np.load(path_perturbed+dataset+'_distances.npy', allow_pickle=True)

In [ ]:
def indices_below_threshold(nested_list, threshold, count_amount=35):
    indices = []
    count=[]
    index=[]
    for i, sublist in enumerate(nested_list):
      count_per_list=0
      indices_per_list = []
      for j, value in enumerate(sublist):
          if value < threshold:
              indices_per_list.append(j)
              count_per_list+=1
      indices.append(indices_per_list)
      count.append(count_per_list)
      if count_per_list > count_amount:
        index.append(i)
    return index, indices

In [ ]:
sample_distances_index_1, ind_1 = indices_below_threshold(d, 1)
len(sample_distances_index_1)

56

In [ ]:
sample_distances_index_15, ind_15  = indices_below_threshold(d, 1.5)
len(sample_distances_index_15)

94

In [ ]:
sample_distances_index_75, ind_75 = indices_below_threshold(d, 0.75, 15)
len(sample_distances_index_75)

34

In [ ]:
sample_distances_index_75

[0,
 1,
 9,
 12,
 19,
 22,
 23,
 27,
 31,
 32,
 33,
 35,
 41,
 42,
 45,
 51,
 53,
 55,
 57,
 66,
 69,
 70,
 73,
 76,
 78,
 80,
 83,
 90,
 96,
 101,
 107,
 108,
 115,
 119]

###loop

In [ ]:
%%timeit
#N_DOCS = len(lipschitz_sample)
MIN_NEIGHBORS_PER_DOC = 15
EPSILON = 0.75 #0.25

shap_lipschitz=[]
max_lipschitz_values=[]
successful_transformer_neighbors=0
for i in sample_distances_index_75:
  print(i)
  original_tokens=tokenizer(lipschitz_sample[i], return_tensors='pt')['input_ids']
  original_text=filter_decode_tokens(original_tokens)
  original_embeds = model.bert.embeddings(original_tokens.to(device))
  original_shap = original_shaps[i]
  successful_transformer_neighbors = 0
  j=0
  while successful_transformer_neighbors < MIN_NEIGHBORS_PER_DOC:
      perturbed_text=perturbed_texts[i][j]
      j+=1
      perturbed_tokens = tokenizer(perturbed_text, return_tensors='pt')['input_ids']
      while len(perturbed_tokens[0]) != len(original_tokens[0]):
        perturbed_tokens =  tokenizer(perturbed_texts[i][j], return_tensors='pt')['input_ids']
        perturbed_text=perturbed_texts[i][j]
        j+=1
        #print(j)
      perturbed_embeds = model.bert.embeddings(perturbed_tokens.to(device))
      d_ij = torch.norm(original_embeds - perturbed_embeds).item() / original_embeds.squeeze().size(0)
      #print(d_ij)
            #if 0 <= d_ij <= EPSILON: is original but didn't work because if d_ij = 0 there would be a division by 0
      if 0 < d_ij <= EPSILON:
            successful_transformer_neighbors += 1
            perturbed_shap = explainer([perturbed_text])
            shap_lipschitz.append([local_lipschitz(original_shap.values, perturbed_shap.values, d_ij)])
            print('successful_transformer_neighbors: '+str(successful_transformer_neighbors))
  print(shap_lipschitz)
  np.save((path_perturbed+dataset+'_'+str(i)+'_lipschitz.npy'), shap_lipschitz)
  max_lipschitz_values.append(max(shap_lipschitz))
  print('max_lipschitz_values: '+ str(max_lipschitz_values))
  if i == sample_distances_index_75[-1]:
    break

0


indexing with dtype torch.uint8 is now deprecated, please use a dtype torch.bool instead. (Triggered internally at ../aten/src/ATen/native/IndexingUtils.h:27.)


  0%|          | 0/272 [00:00<?, ?it/s]

successful_transformer_neighbors: 1


  0%|          | 0/272 [00:00<?, ?it/s]

...

successful_transformer_neighbors: 9


  0%|          | 0/306 [00:00<?, ?it/s]

Partition explainer: 2it [00:13, 13.52s/it]               


successful_transformer_neighbors: 10


KeyboardInterrupt: ignored

In [ ]:
print(shap_lipschitz)

NameError: ignored

In [ ]:
np.save(path_pertrubed+dataset+'lipschitz.npy', shap_lipschitz)

In [ ]:
max_lipschitz_values

NameError: ignored